# TMA4320 Introduksjon til vitenskapelige beregninger
## Øving 1

### Oppgave 1 (Feilsøking og retting. Dokumentasjon).

I denne oppgaven skal du beregne tilnærmelser til integraler ved hjelp av [Simpsons metode](https://wiki.math.ntnu.no/tma4100/tema/numerics?&#numerisk_integrasjon)

\begin{equation}
\int_a^b f(x)\mathrm{d}x \simeq S_{n} = \frac{h}{3}\left( f(x_0)+4\sum_{i=1}^{n/2}f(x_{2i-1}) + 2\sum_{i=1}^{n/2-1} f(x_{2i}) + f(x_{n}) \right)
\end{equation}
der $h=(b-a)/n$, der $n$ må være et like tall, og $x_i=a+ih$.

Under er det et forslag til en kode, skrevet etter prinsippet raskt og gæli. Oppgaven går ut på: 

* Debug koden, både for syntaksfeil og logiske feil. Kan den forbedres på andre måter?
* Skriv den om til en funksjon. Test funksjonen på et passende utvalg med testproblemer. 
* Dokumenter koden. 

Forslag til testproblemer med kjent løsning.

1. $\int_1^2 x^2\mathrm{d}x = 7/3$. I dette tilfellet skal Simpsons formel levere et eksakt resultat. (Hvorfor?)
2. $\int_0^{\pi/2} \sin{x} \mathrm{d}x = 1$. 

Finn gjerne på noen egne testproblemer også. 

**Hint**
* Er det problemer med logiske feil, sett $n=2$, utfør regningene på papir, og sammenlign med hva som skjer i koden. 
* Flytt koden over til Spyder eller en annen IDE, og debug koden der. 

In [ ]:
# Eksempel 1
from math import sin, pi
def f(x):
    return x**2
a, b = 1, 2
eksakt = 7/3

In [ ]:
# Eksempel 2
def f(x):
    return sin(x)
a, b = 0, pi/2
eksakt = 1.0

#### Forslag til løsning:

In [ ]:
def simpson(f, a, b, n=10):
    '''
    Compute an approximation to an integral by Simpson's method
    Input: 
        f:    The function
        a, b: The integration interval
        n:    Number of intervals (an even number)
    Output:
        The approximation S(2n)
    '''
    h = (b-a)/n        
    
    S = f(a)
    for i in range(1,int(n/2)+1):    # Sum over the odd grid points
        x = a+(2*i-1)*h
        S = S + 4*f(x)
    for i in range(1, int(n/2)):     # Sum over the even grid points
        x = a+2*i*h
        S = S + 2*f(x)
    S = S + f(b)
    S = h*S/3                        # Final result
    return S

In [ ]:
# Forutsetter at cellen med et av eksemplene allerede er kjørt.
S = simpson(f, a, b, n=10)
feil = abs(S-eksakt)
print(f'S = {S:.4f}, feil = {feil:.3e}')

### Oppgave 2 (Numpy)

Implementer Simpsons metode igjen, men denne gangen ved bruk av numpy. For eksempel ved: 
* Lag et array av gridpunktene $\{x_i\}_{i=0}^n$ ved bruk av <tt>np.linspace</tt>
* For de to summene i uttrykket for Simpson's metode: Plukk ut de riktige gridpunktene $x_i$, finn funksjonsverdien av disse, og bruk <tt>np.sum</tt>. 
* Legg til funksjonsverdiene i de to endepunktene, multipliser med $h/3$.  

#### Forslag til løsning

In [ ]:
import numpy as np

# Eksempel 2
def f(x):
    return np.sin(x)
a, b = 0.0, 0.5*np.pi
eksakt = 1.0

def simpson_v2(f, a, b, n=10):
    ''' Kortversjonen av Simpsons metode'''
    h = (b-a)/n
    x = np.linspace(a,b,n+1)
    return h*(f(x[0])+4*np.sum(f(x[1::2]))+2*np.sum(f(x[2:-1:2]))+f(x[-1]))/3


S = simpson_v2(f, a, b, n=20)
print(f'S = {S:.4f}, feil = {feil:.3e}')
    

### Oppgave 4 (Kompleksitet. Effektiv bruk av Numpy)

La $A,B\in \mathbb{R}^{n \times n}$. Produktet $C=AB$ regnes ut ved følgende algoritme:

$$
\text{for } i=1,\cdots,n \\
\qquad \text{for } j=1,\cdots,n \\
\qquad \qquad c_{ij} = \sum_{k=1}^n a_{ik} b_{kj}. 
$$
 
**a)**

Hvor mange flyttallsoperasjoner krever en slik matrise-matrise multiplikasjon av to $n\times n$-matriser? 

**Svar** Denne operasjoner krever $n^3$ multiplikasjoner og $n^2(n-1)$ addisjoner. Regner vi en flyttallsoperasjon (flop) som en addisjon og en multiplikasjon kreves altså $n^3$ flop. 

Poenget med resten av denne oppgaven er hovedsaklig å vise hvor effektive Pythons innebygde rutiner for lineær algebra er. 

**b)** Skriv din egen rutine for å regne ut matrise-matrise produktet $C=BA$ med algoritmen over. 

Deretter: Velg $n$. Lag to tilfeldige $n\times n$-matriser $A$ og $B$. Regn ut $C=AB$ med din egen rutine. Ta tiden. Sammenlign med den tiden det tar å gjøre samme operasjon med pythons multiplikasjonsoperator `@` eller `np.dot`. 

Gjenta gjerne eksperimentet med din egen `gauss_pivot` og `np.linalg.solve`. Velg høyreside selv. 

In [ ]:
def mult(A,B):
    ''' 
    Regner ut matrise-matrise produktet C=AB
    '''
    na, ma = np.shape(A)
    nb, mb = np.shape(B)
    assert ma==nb, 'A and B are not compatible'
    C = np.zeros((na, mb))
    for i in range(na):
        for j in range(mb):
            for k in range(nb):
                C[i,j] += A[i,k]*B[k,j]
    return C

In [ ]:
# Lag matrisene
n = 100
A = np.random.randn(n,n)
B = np.random.randn(n,n)

# Test egen kode:
import time
tstart = time.time()
C = mult(A,B)
print(f'Min kode bruker     {time.time()-tstart:.3e} s')

# Test pythons kode
tstart = time.time()
C = A@B
print(f'Pyhtons kode bruker {time.time()-tstart:.3e} s')

In [ ]:
# Alternativ (og mer nøyaktig metode) for å måle tidsbruk:

%timeit mult(A,B)
%timeit A@B